# An ensemble method for top-N recommendations from the SVD

## SVD

In [1]:
import pandas as pd
import numpy as np
import scipy.sparse as sp
from scipy.sparse.linalg import svds
import pickle
import copy 
import random

In [2]:
data_file = pd.read_table('data/training.csv', sep = ',', header=None, engine='python')
data_file.shape

(700146, 4)

In [3]:
#movies 3666(gercege karşılık gelen index) alıp 3952(gerçekid) döner, movie_indices 3952 alıp 3666 döner
users = np.unique(data_file[0]) # 1(0.idex) den 6040(6039.index) a kadar
movies = np.unique(data_file[1]) # 1(0.idex) den 3952(3666.idex) ye kadar

number_of_rows = len(users) #6040
number_of_columns = len(movies) #3667

movie_indices, user_indices = {}, {}
 
for i in range(len(movies)):
    movie_indices[movies[i]] = i # movie_indices[3952] = 3666 x.filmin indisini verir
    
for i in range(len(users)):
    user_indices[users[i]] = i # x.userın indisini verir

In [4]:
V = sp.lil_matrix((number_of_rows, number_of_columns))
for line in data_file.values:
    u, i , r , gona = map(int,line)
    V[user_indices[u], movie_indices[i]] = r # gerçek user ve movie idnin indexini bulup ratingi matrixteki yere atar

In [5]:
print(users)
print(user_indices[6000])
print(movies)
print(movie_indices[3952])
#print (V[:3,:])

[   1    2    3 ..., 6038 6039 6040]
5999
[   1    2    3 ..., 3950 3951 3952]
3666


In [6]:
print(movies[253])
print(movies[20])
print(movies[0])
print(movies)

260
21
1
[   1    2    3 ..., 3950 3951 3952]


In [7]:
u,s, vt = svds(V, k = 16)

In [8]:
s_diag_matrix = np.zeros((s.shape[0], s.shape[0]))

for i in range(s.shape[0]):
    s_diag_matrix[i,i] = s[i]

In [9]:
X_lr = np.dot(np.dot(u, s_diag_matrix), vt)

In [10]:
negcounter = 0
poscounter = 0
for i in range(s.size-1,s.size):
    for factor in vt[i,:]:
        if factor > 0:
            poscounter = poscounter + 1
        else:
            negcounter = negcounter + 1
print(negcounter,poscounter)

(0, 3667)


In [11]:
X_lr[0,2354]

-0.00073581194249325386

In [12]:
#X_lr.tofile(file = 'data/svdresults.csv', sep = "::")

In [13]:
print(u.shape)
deneme = np.dot(u, vt)


(6040, 16)


In [14]:
print(X_lr.shape, V.shape, deneme.shape)

((6040, 3667), (6040, 3667), (6040, 3667))


In [15]:
print(user_indices[641],movie_indices[1210],user_indices[4388],movie_indices[3270],user_indices[1448],movie_indices[3270])
print(user_indices[641],movie_indices[2424],user_indices[1280],movie_indices[3826],user_indices[4034],movie_indices[3578])
print(user_indices[4779],movie_indices[1237],user_indices[588],movie_indices[1288],user_indices[4578],movie_indices[1120])
print(user_indices[1100],movie_indices[3159],user_indices[4604],movie_indices[2003],user_indices[4578],movie_indices[1120])

(640, 1108, 4387, 3017, 1447, 3017)
(640, 2206, 1279, 3546, 4033, 3305)
(4778, 1134, 587, 1184, 4577, 1033)
(1099, 2916, 4603, 1801, 4577, 1033)


In [16]:

print(V[1279, 3546],X_lr[1279, 3546],deneme[1279, 3546])
print(V[1099, 2916],X_lr[1099, 2916],deneme[1099, 2916])

print(V[4603, 1801],X_lr[4603, 1801],deneme[4603, 1801])

print(V[4033, 3305],X_lr[4033, 3305],deneme[4033, 3305])
print(V[640, 1108],X_lr[640, 1108],deneme[640, 1108])
print(V[4387, 3017],X_lr[4387, 3017],deneme[4387, 3017])

print(V[640, 2206],X_lr[640, 2206],deneme[640, 2206])
print(V[587, 1184],X_lr[587, 1184],deneme[587, 1184])
print(V[4577, 1033],X_lr[4577, 1033],deneme[4577, 1033])

print(V[1447, 2760],X_lr[1447, 2760],deneme[1447, 2760])
print(V[4778, 1134],X_lr[4778, 1134],deneme[4778, 1134])


(1.0, 0.22068542912970082, 0.00061929466237305869)
(1.0, 0.78137732828072515, 0.0021025451863780722)
(2.0, 0.39157929549244647, 0.00085796575291467671)
(3.0, 0.36122329138466891, -0.00089513061707196151)
(3.0, 2.5404778637796768, 0.0053831951973065603)
(3.0, 0.36185913563878203, 0.00021694145057815561)
(4.0, 0.13089658866036757, -0.00017588812303208565)
(4.0, 3.313097972718865, 0.005543548540291778)
(4.0, 1.5256565641554447, 0.0025832632604163006)
(5.0, 1.0722291146263006, -0.0067962885577380608)
(5.0, 1.2502592441398561, 0.0031777084912169729)


In [13]:
print(np.min(X_lr))

-2.58569180878


##  Model for Top-N Recommendations

In [14]:
class Node:
    def __init__(self,fsize):
        self.itemFactors = np.empty(shape = (fsize,0))
        self.userFactors = np.empty(shape = (fsize,0))
        self.itemList = []
        self.userList = []
        self.factor = None
        self.factors = []
        self.score = 0
        self.left = None
        self.right = None

In [20]:
def fillLists(V):
    for user in user_indices:
        V.userList.append(user-1)
    for item in movie_indices:
        V.itemList.append(item-1)
def restartV():
    V = Node(s.size)
    V.itemFactors = vt
    V.userFactors = u
    fillLists(V)
    factors = []
    factors.extend(range(0,s.size))
    V.factors = factors
    return V
V = restartV()
print(len(V.userList))

6040


In [21]:
def printNode(node):
    print("itemFactors :") 
    #print(node.itemFactors)
    print(node.itemFactors.shape)
    print("userFactors :")
    #print(node.userFactors)
    print(node.userFactors.shape)
    print("factor :")
    print(node.factor)
    print("score :")
    print(node.score)
    print("left :")
    print(node.left)
    print("right :")
    print(node.right)
def printTree(node):
    printNode(node)
    if (node.left != None):
        print("LEFT :")
        printTree(node.left)
    if (node.right != None):
        print("RIGHT :")
        printTree(node.right)
def countLeaves(node):
    count = 0
    if (node.left != None):
        if (node.left.itemFactors.shape[1] <= 300):
            count += 1
        else:
            count += countLeaves(node.left)
    else:
        print(node.itemFactors.shape[1])
        print("ERROR")
    if (node.right != None):
        if (node.right.itemFactors.shape[1] <= 300):
            count += 1
        else:
            count += countLeaves(node.right)
    else:
        print(node.itemFactors.shape[1])
        print("ERROR")
    return count

In [22]:
V.itemFactors.shape

(16, 3667)

In [23]:
V.userFactors.shape

(6040, 16)

In [24]:
def splitNode(node, factor):
    #print("splitNode: ", node.factors, factor)
    factorIndex = node.factors.index(factor)
    node.left = Node(len(node.factors))
    node.right = Node(len(node.factors))
    node.left.factors = node.factors
    node.right.factors = node.factors
    left = 0 #flag and counter
    right = 0
    empt = Node(len(node.factors))
    
    node.right.userFactors = np.transpose(node.right.userFactors)
    node.left.userFactors = np.transpose(node.left.userFactors)
    node.right.itemFactors = np.transpose(node.right.itemFactors)
    node.left.itemFactors = np.transpose(node.left.itemFactors)
    
    
    #print("item: ", node.itemFactors.shape, factor, len(node.itemList))
    #print("user: ", node.userFactors.shape, factor, len(node.userList))
    if (np.array_equal(node.itemFactors, empt.itemFactors) == False):   #bos item factor girebilir mi cond dene
    #if (len(node.itemFactors.shape) > 1):   #bos item factor girebilir mi cond dene
        #print(node.itemFactors.shape)
        for i in range(node.itemFactors.shape[1]):
            #print(node.itemFactors[:, i])
            if (node.itemFactors[:, i][factorIndex] >= 0 ):
                if (left == 0):
                    node.left.itemFactors = node.itemFactors[:, i]
                else:
                    node.left.itemFactors = np.vstack((node.left.itemFactors, node.itemFactors[:, i]))
                node.left.itemList.append(node.itemList[i])
                left += 1
            else:
                #continue
                if (right == 0):
                    node.right.itemFactors = node.itemFactors[:, i]
                else:
                    node.right.itemFactors =np.vstack((node.right.itemFactors, node.itemFactors[:, i]))
                node.right.itemList.append(node.itemList[i])
                right += 1
        node.left.itemFactors = np.transpose(node.left.itemFactors)
        node.right.itemFactors = np.transpose(node.right.itemFactors)
    else:
        print('itemFactors not available')
    left = 0
    right = 0
    if (np.array_equal(node.userFactors, empt.userFactors) == False):   #bos user factor girebilme ihtimali dusun
    #if (len(node.userFactors.shape) > 1):   #bos user factor girebilme ihtimali dusun
        #print(node.userFactors.shape)
        for i in range(node.userFactors.shape[0]):
            if (node.userFactors[i, :][factorIndex] >= 0 ):
                if (left == 0):
                    node.left.userFactors = node.userFactors[i, :]
                else:
                    node.left.userFactors = np.vstack((node.left.userFactors, node.userFactors[i, :]))
                node.left.userList.append(node.userList[i])
                left += 1
            else:
                if (right == 0):
                    node.right.userFactors = node.userFactors[i, :]
                else:
                    node.right.userFactors = np.vstack((node.right.userFactors, node.userFactors[i, :]))
                node.right.userList.append(node.userList[i])
                right += 1
    else:
        print('userFactors not available')
    node.score =  computePrecision(node)

In [25]:
def findTopN(matrix, N):
    #print(matrix.shape)
    newMatrix = matrix.argsort(axis = 1)
    newMatrix = np.fliplr(newMatrix)
    return newMatrix[:,:N]
    

In [26]:
mx = findTopN(X_lr, 5)
print(mx)
print(mx.shape)
print(mx[6039,:])

[[ 511  309  847 1014 1096]
 [1826  511 2626  106  309]
 [1096  253 1094 2626 1095]
 ..., 
 [1095    0 2178 1047 1161]
 [ 847  832  840  838  841]
 [2626  511  590  793 1092]]
(6040, 5)
[2626  511  590  793 1092]


In [27]:
precisionAt = 5
def computePrecision(node):
    
    diag_matrix = np.zeros((len(node.factors), len(node.factors)))
    for i in range(len(node.factors)):
        diag_matrix[i,i] = s_diag_matrix[node.factors,node.factors][i]
    
    relevantRight = np.dot(np.dot(node.right.userFactors,diag_matrix), node.right.itemFactors)
    relevantLeft = np.dot(np.dot(node.left.userFactors,diag_matrix), node.left.itemFactors)
    topRight = findTopN(relevantRight, precisionAt)
    topLeft = findTopN(relevantLeft, precisionAt)
    #print(topRight.shape)
    #print(topLeft.shape)
    
    samePlace = 0
    inTopN = 0
    for u in range(len(node.left.userList)):
        #print(u)
        #print(node.left.userList[u])
        for i in range(precisionAt):
            #print(node.left.itemList[topLeft[0,:][i]])
            if (node.left.itemList[topLeft[u,:][i]] == mx[node.left.userList[u],:][i]):
                #print("ALLAH")
                #print(node.left.itemList[topLeft[u,:][i]])
                #print(mx[node.left.userList[u],:])
                samePlace += 1
            if node.left.itemList[topLeft[u,:][i]] in mx[node.left.userList[u],:]:
                inTopN += 1
    for u in range(len(node.right.userList)):
        #print(u)
        #print(node.right.userList[u])
        for i in range(precisionAt):
            #print(node.right.itemList[topRight[0,:][i]])
            if (node.right.itemList[topRight[u,:][i]] == mx[node.right.userList[u],:][i]):
                #print(node.right.itemList[topRight[u,:][i]])
                #print(mx[node.right.userList[u],:])
                samePlace += 1
            if node.right.itemList[topRight[u,:][i]] in mx[node.right.userList[u],:]:
                inTopN += 1
    #print(samePlace)
    #print(inTopN)
    ret = float(inTopN)/(len(node.userList)*precisionAt)
    #ret = float(samePlace)/(len(node.userList)*precisionAt)
    print(ret)
    return ret
    

In [28]:
splitNode(V, 15)

0.034238410596


In [29]:
def buildTree(node, factors):
    #printNode(node)
    print(factors)
    # TODO : user yoksa bolunmeyi durdur
    if (len(node.itemFactors.shape) > 1 and node.itemFactors.shape[1] <= 300):
        print("Threshold value is reached")
        return node
    elif (len(node.itemFactors.shape) <= 1):
        print('one item factor')
        return node
    elif (node.itemFactors.shape[1] == 0):
        print('no item factor')
        return node
    winner = Node(len(node.factors))
    if not factors:
        print('factors empty')
        return node
    for factor in factors:
        node.factor = factor
        splitNode(node,factor)
        if (node.score >= winner.score):
            winner = copy.deepcopy(node) 
    #print(winner.score)
    #print(winner.factor)
    factors.remove(winner.factor)
    node.factor = winner.factor
    lfactors = list(factors)
    rfactors = list(factors)
    node.left = buildTree(winner.left, lfactors)     # TODO : validate
    node.right = buildTree(winner.right, rfactors)   # TODO : validate
    return node
    

In [30]:
print(V.itemFactors.shape)
print(V.userFactors.shape)

(16, 3667)
(6040, 16)


In [31]:
splitNode(V,0)
print(V.right.itemFactors.shape)
print(V.left.itemFactors.shape)
print(V.right.userFactors.shape)
print(V.left.userFactors.shape)
printNode(V)

0.0247350993377
(16, 2203)
(16, 1464)
(3298, 16)
(2742, 16)
itemFactors :
(16, 3667)
userFactors :
(6040, 16)
factor :
None
score :
0.0247350993377
left :
<__main__.Node instance at 0x7f93aef1ac68>
right :
<__main__.Node instance at 0x7f93aad69170>


In [32]:
V = restartV()
factors = []
factors.extend(range(0,s.size))
V = buildTree(V,factors)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]
0.0247350993377
0.0237417218543
0.0247350993377
0.0290728476821
0.0251986754967


KeyboardInterrupt: 

In [33]:
print("ROOT :")
printTree(V)

ROOT :
itemFactors :
(16, 3667)
userFactors :
(6040, 16)
factor :
5
score :
0.0251986754967
left :
<__main__.Node instance at 0x7f93aef1a248>
right :
<__main__.Node instance at 0x7f93aef1a1b8>
LEFT :
itemFactors :
(16, 1510)
userFactors :
(3178, 16)
factor :
None
score :
0
left :
None
right :
None
RIGHT :
itemFactors :
(16, 2157)
userFactors :
(2862, 16)
factor :
None
score :
0
left :
None
right :
None


In [43]:
countLeaves(V)

ERROR
ERROR
ERROR
ERROR


0

In [34]:
def getFactorGroups(size, p, a):
    groups = []
    for i in range(0,a):
        counterList = np.zeros(len(factors))
        for c in range(0,int(1/p)):
            group = []
            while (len(group) < size * p):
                available = []
                for k in range(len(counterList)):
                    if (counterList[k] < 1 and k not in group):
                        available.append(k)
                factor = available[random.randint(0, len(available)-1)]
                counterList[factor] = counterList[factor] + 1 
                group.append(factor)
            group.sort()
            groups.append(group)
    return groups
            

In [35]:
def buildForest(factors, p, a, sl):
    forest = []
    groups = getFactorGroups(len(factors), p, a)
    for group in groups:
        print(group)
        V = Node(len(group))
        V.itemFactors = vt[group,:]
        V.userFactors = u[:,group]
        fillLists(V)
        V.factors = group
        buildTree(V,group)
        forest.append(V)
    return forest

In [36]:
factors = []
factors.extend(range(0,16))
forest = buildForest(factors, 0.5, 3, 300)

[3, 4, 6, 7, 10, 12, 13, 14]
[3, 4, 6, 7, 10, 12, 13, 14]
0.0164900662252
0.0142715231788
0.0167880794702
0.0114900662252
0.00913907284768
0.011821192053
0.0141059602649
0.0124503311258
[3, 4, 7, 10, 12, 13, 14]
0.0340206185567
0.0278350515464
0.0218703976436
0.0181148748159
0.0262150220913
0.0273932253314
0.0249631811487
[4, 7, 10, 12, 13, 14]
0.022494592646
0.0170151405912
0.0167267483778
0.0282624369142
0.022494592646
0.018601297765
[4, 7, 10, 13, 14]
Threshold value is reached
[4, 7, 10, 13, 14]
0.00376175548589
0.00376175548589
0.00564263322884
0.00438871473354
0.00313479623824
[4, 7, 13, 14]
Threshold value is reached
[4, 7, 13, 14]
0.0046511627907
0.0015503875969
0.0077519379845
0.0015503875969
[4, 7, 14]
Threshold value is reached
[4, 7, 14]
0.00697674418605
0.00232558139535
0.00232558139535
[7, 14]
Threshold value is reached
[7, 14]
Threshold value is reached
[4, 7, 10, 12, 13, 14]
0.0299473288187
0.025583145222
0.0192626034612
0.0213694507148
0.0297968397291
0.0287434161023
[

In [40]:
print(forest)

[<__main__.Node instance at 0x7f93aad691b8>, <__main__.Node instance at 0x7f93aad693b0>, <__main__.Node instance at 0x7f93aef0a6c8>, <__main__.Node instance at 0x7f93aad69320>, <__main__.Node instance at 0x7f93afe54b00>, <__main__.Node instance at 0x7f93afd1bbd8>]


In [42]:
for node in forest:
    print(countLeaves(node))

20
24
24
18
26
19


In [43]:
printTree(forest[3])

itemFactors :
(8, 3667)
userFactors :
(6040, 8)
factor :
2
score :
0.00592715231788
left :
<__main__.Node instance at 0x7f93afd1b6c8>
right :
<__main__.Node instance at 0x7f93afd521b8>
LEFT :
itemFactors :
(8, 1423)
userFactors :
(2928, 8)
factor :
6
score :
0.00833333333333
left :
<__main__.Node instance at 0x7f93afd1bfc8>
right :
<__main__.Node instance at 0x7f93afd1bea8>
LEFT :
itemFactors :
(8, 681)
userFactors :
(1388, 8)
factor :
0
score :
0.0174351585014
left :
<__main__.Node instance at 0x7f93afcd2518>
right :
<__main__.Node instance at 0x7f93afcd24d0>
LEFT :
itemFactors :
(8, 288)
userFactors :
(673, 8)
factor :
None
score :
0
left :
None
right :
None
RIGHT :
itemFactors :
(8, 393)
userFactors :
(715, 8)
factor :
7
score :
0.000559440559441
left :
<__main__.Node instance at 0x7f93afcd2758>
right :
<__main__.Node instance at 0x7f93afcd2710>
LEFT :
itemFactors :
(8, 181)
userFactors :
(406, 8)
factor :
None
score :
0
left :
None
right :
None
RIGHT :
itemFactors :
(8, 212)
userFa

# # Testing Model

In [44]:
test_file = pd.read_table('data/test.csv', sep = ',', header=None, engine='python')
test_file.shape

(300063, 4)

In [45]:
#movies 3666(gercege karşılık gelen index) alıp 3952(gerçekid) döner, movie_indices 3952 alıp 3666 döner
test_users = np.unique(test_file[0]) # 1(0.idex) den 6040(6039.index) a kadar
test_movies = np.unique(test_file[1]) # 1(0.idex) den 3952(3666.idex) ye kadar

test_number_of_rows = len(test_users) #6040
test_number_of_columns = len(test_movies) #3667

test_movie_indices, test_user_indices = {}, {}
 
for i in range(len(test_movies)):
    test_movie_indices[test_movies[i]] = i # movie_indices[3952] = 3666 x.filmin indisini verir
    
for i in range(len(test_users)):
    test_user_indices[test_users[i]] = i # x.userın indisini verir
print(len(test_movie_indices), len(movie_indices))

(3530, 3667)


In [46]:
test_V = sp.lil_matrix((test_number_of_rows, number_of_columns))
for line in test_file.values:
    test_u, test_i , test_r , test_gona = map(int,line)
    if test_i in movie_indices:
        print(test_user_indices[test_u],movie_indices[test_i],r)
        test_V[test_user_indices[test_u], movie_indices[test_i]] = test_r # gerçek user ve movie idnin indexini bulup ratingi matrixteki yere atar
    else:
        print("kekt",test_user_indices[test_u],test_i,r)

(5753, 335, 4)
(1145, 448, 4)
(3106, 202, 4)
(2837, 2970, 4)
(2291, 2951, 4)
(4003, 3575, 4)
(5466, 1054, 4)
(5134, 771, 4)
(4982, 2906, 4)
(5945, 2794, 4)
(305, 1155, 4)
(5487, 2322, 4)
(1769, 2250, 4)
(5826, 1826, 4)
(3042, 937, 4)
(1439, 997, 4)
(2100, 1809, 4)
(3758, 464, 4)
(5298, 852, 4)
(4713, 2072, 4)
(2302, 3305, 4)
(2965, 2948, 4)
(3655, 458, 4)
(4379, 3451, 4)
(5346, 2596, 4)
(4979, 2264, 4)
(3490, 1255, 4)
(4517, 1813, 4)
(4817, 265, 4)
(2483, 1007, 4)
(3943, 2993, 4)
(3519, 3327, 4)
(4635, 1809, 4)
(3761, 1116, 4)
(691, 2686, 4)
(5697, 2309, 4)
(4651, 2123, 4)
(1529, 2153, 4)
(746, 3606, 4)
(1421, 2846, 4)
(5901, 1392, 4)
(1131, 2413, 4)
(2019, 3424, 4)
(3681, 49, 4)
(5304, 3184, 4)
(44, 1524, 4)
(2805, 332, 4)
(1732, 2263, 4)
(1838, 354, 4)
(5858, 33, 4)
(530, 970, 4)
(4779, 3044, 4)
(5315, 3257, 4)
(1169, 1744, 4)
(1070, 9, 4)
(4086, 370, 4)
(736, 1110, 4)
(4624, 1384, 4)
(4973, 1184, 4)
(619, 398, 4)
(950, 1816, 4)
(3150, 1803, 4)
(6005, 1596, 4)
(1289, 836, 4)
(3683, 2

In [48]:
test_u,test_s, test_vt = svds(test_V, k = 16)

In [49]:
test_s_diag_matrix = np.zeros((test_s.shape[0], test_s.shape[0]))

for i in range(test_s.shape[0]):
    test_s_diag_matrix[i,i] = test_s[i]
    
test_X_lr = np.dot(np.dot(test_u, test_s_diag_matrix), test_vt)

In [50]:
test_u.shape

(6039, 16)

In [51]:
def isLeaf(node):
    #print(node.itemFactors.shape)
    if len(node.itemFactors.shape) < 2:
        print("error")
    elif node.itemFactors.shape[1] < 300:
        print("zaa")
        return True
    return False
def isEmpty(node):
    empt = Node(len(node.factors))
    if np.array_equal(node.itemFactors, empt.itemFactors):
        return True
    return False

In [55]:
def recommend(userFactors):
    topList = np.empty(shape = (precisionAt,0))
    topIndexList = []
    counter = 0
    for tree in forest:
        node = tree
        while not isLeaf(node):
            if userFactors[node.factor] >= 0:
                if not isEmpty(node.left):
                    node = node.left
                else:
                    break
            else:
                if not isEmpty(node.right):
                    node = node.right
                else:
                    break
        #print(userFactors[node.factors])
        print(node.itemFactors.shape, node.userFactors.shape)
        
        test_diag_matrix = np.zeros((len(node.factors), len(node.factors)))
        for i in range(len(node.factors)):
            test_diag_matrix[i,i] = test_s_diag_matrix[node.factors,node.factors][i]
        
        relevant = np.dot(np.dot(userFactors[node.factors],test_diag_matrix), node.itemFactors)
        #print(relevant)
        indexMatrix = relevant.argsort()[::-1][:precisionAt]
        dotMatrix = relevant[indexMatrix]
        indexList = []
        print(topList.shape, dotMatrix.shape)
        for i in indexMatrix:
            #print(node.itemList[i], i)
            indexList.append(node.itemList[i])
        print(indexList)
        if counter < 1:
            topList = dotMatrix
        else:
            topList = np.vstack((topList, dotMatrix))
        topIndexList.append(indexList)
        counter += 1
    print(topList)
    print(topIndexList)

In [56]:
recommend(test_u[1])

zaa
((8, 193), (322, 8))
((5, 0), (5,))
[2699, 550, 234, 2760, 561]
zaa
((8, 146), (771, 8))
((5,), (5,))
[2689, 3611, 1918, 3624, 2196]
((8, 393), (1976, 8))
((2, 5), (5,))
[2699, 1273, 1964, 1147, 550]
zaa
((8, 288), (673, 8))
((3, 5), (5,))
[363, 46, 594, 593, 2267]
((8, 488), (1633, 8))
((4, 5), (5,))
[2086, 2095, 1021, 1032, 2136]
zaa
((8, 158), (182, 8))
((5, 5), (5,))
[744, 1844, 2911, 372, 1833]
[[ 0.4813669   0.37181031  0.28546241  0.19697976  0.19094287]
 [ 0.01316001  0.00815455  0.00357675  0.0023874   0.00175669]
 [ 0.25106374  0.21527539  0.1925072   0.18333793  0.18301048]
 [ 0.33379097  0.3213335   0.29794884  0.26298506  0.25584283]
 [ 0.11284064  0.1099965   0.10690396  0.10568504  0.10188361]
 [ 0.27027507  0.20792051  0.1794765   0.16711445  0.16595476]]
[[2699, 550, 234, 2760, 561], [2689, 3611, 1918, 3624, 2196], [2699, 1273, 1964, 1147, 550], [363, 46, 594, 593, 2267], [2086, 2095, 1021, 1032, 2136], [744, 1844, 2911, 372, 1833]]


In [57]:
print(test_u[1])

[ 0.01497272 -0.00615603  0.00744261 -0.00430182  0.00403475 -0.00688191
  0.00216375  0.01259327 -0.00293882 -0.00355286 -0.03195536  0.00639205
 -0.00476632 -0.00156713  0.00511973 -0.00926155]


In [114]:
def deliverRecommendations(user):
    for tree in forest:
        findItem(tree,user)
    
    
    

In [116]:
deliverRecommendations(u[0,:])

[-0.00393761 -0.00410995 -0.00802113 -0.00287964  0.00548483 -0.00799127
  0.008842    0.01735936  0.00127831 -0.00278285  0.00823601  0.01432085
 -0.00023553 -0.00218184 -0.00175933  0.00405338]
[-0.00393761 -0.00410995 -0.00802113 -0.00287964  0.00548483 -0.00799127
  0.008842    0.01735936  0.00127831 -0.00278285  0.00823601  0.01432085
 -0.00023553 -0.00218184 -0.00175933  0.00405338]
[-0.00393761 -0.00410995 -0.00802113 -0.00287964  0.00548483 -0.00799127
  0.008842    0.01735936  0.00127831 -0.00278285  0.00823601  0.01432085
 -0.00023553 -0.00218184 -0.00175933  0.00405338]
[-0.00393761 -0.00410995 -0.00802113 -0.00287964  0.00548483 -0.00799127
  0.008842    0.01735936  0.00127831 -0.00278285  0.00823601  0.01432085
 -0.00023553 -0.00218184 -0.00175933  0.00405338]
[-0.00393761 -0.00410995 -0.00802113 -0.00287964  0.00548483 -0.00799127
  0.008842    0.01735936  0.00127831 -0.00278285  0.00823601  0.01432085
 -0.00023553 -0.00218184 -0.00175933  0.00405338]
[-0.00393761 -0.0041